In [1]:
import sys; sys.path.append('../3rdparty/ElasticRods/python')
import elastic_rods, elastic_knots
import numpy as np, matplotlib.pyplot as plt, time, io, os
from scipy.sparse import coo_matrix
from scipy.sparse.linalg import eigsh

from helpers import *
from parametric_curves import *
import py_newton_optimizer 

from linkage_vis import LinkageViewer as Viewer, CenterlineViewer
from tri_mesh_viewer import PointCloudViewer, PointCloudMesh

%load_ext autoreload
%autoreload 2

import parallelism
parallelism.set_max_num_tbb_threads(1)

from MEP import MEP

In [2]:
start_file = "../data/L400-r0.2-UpTo9Crossings/4_1/0033.obj"
goal_file = "../data/L400-r0.2-UpTo9Crossings/4_1/0001.obj"
mep = MEP(start_file,goal_file)

In [3]:
cp = mep.getContactProblem()
H = cp.hessian()

triplets = list(H.entries())

rows = np.array([t.i for t in triplets])
cols = np.array([t.j for t in triplets])
vals = np.array([t.v for t in triplets])

# Matrixgröße aus den Indizes ableiten
n_rows = int(rows.max()) + 1
n_cols = int(cols.max()) + 1

# Sparse-Matrix aufbauen
H_sparse = coo_matrix((vals, (rows, cols)), shape=(n_rows, n_cols)).tocsr()

# Kleinster Eigenwert & Eigenvektor (negativer Modus)
eigvals, eigvecs = eigsh(H_sparse, k=1, which='SA')

min_eigval = eigvals[0]
Nhat = eigvecs[:, 0] / np.linalg.norm(eigvecs[:, 0])

print(f"Kleinster Eigenwert: {min_eigval}")
print(f"Nhat shape: {Nhat.shape}")


Kleinster Eigenwert: -1841.307267445252
Nhat shape: (401,)


# set dimers

In [4]:
R = cp.getDoFs() #midpoint of dimer
N = np.random.rand(len(R)) 
Nhat = N / np.linalg.norm(N) # random unit vector
delta = 0.01 #distance of R1 and R2
R1 = R + delta * Nhat
R2 = R - delta * Nhat

# get the Energy for R1 and R2

In [5]:
def getForce(R):
    cp.setDoFs(R)
    return - cp.gradient()


F1 = getForce(R1)
F2 = getForce(R2)
F0 = (F1 + F2) /2 #mean force

# compute the curvature  C

In [6]:
def curvature (F1, F2, Nhat, delta):
    C = np.dot((F2 - F1),Nhat ) / (2 * delta)
    return C

C = curvature(F1,F2,Nhat,delta)

In [7]:
def perpForce(F1, F2, Nhat):
    F1_perp = F1 - np.dot(F1, Nhat) * Nhat
    F2_perp = F2 - np.dot(F2, Nhat) * Nhat
    F_perp = F1 - F2
    theta = F_perp / np.linalg.norm(F_perp)
    return F_perp, theta 

F_perp, theta = perpForce(F1, F2, Nhat)
F_par = np.dot(F0, Nhat)* Nhat

# Rotate the dimer
First Rotate and then estimate the best rotaion


In [8]:
def rotateDimer(angle, R,Nhat, theta, delta):
    R1 = R + (Nhat* np.cos(angle) + theta * np.sin(angle))*delta
    N = R1 - R 
    Nhat = N / np.linalg.norm(N)

    R1 = R + delta * Nhat
    R2 = R - delta * Nhat
    return R1, R2, Nhat

def scalarRotationalForce(F_perp, theta, delta):
    F = np.dot(F_perp, theta)/delta 
    return F

def dScalarRotationalForce(F_star, theta_star,F, theta, d_angle):
    dF = (np.dot(F_star, theta_star) - np.dot(F, theta))/d_angle
    return dF


def rotationEstimate(F, theta, F_star, theta_star, dF):
    angle = - (np.dot(F, theta) + np.dot(F_star, theta_star) )/ (2* dF)
    return angle

In [9]:
def estimateAngle(R, Nhat,theta, delta, angle = 0.1):
    
    R1_star, R2_star , Nhat_star = rotateDimer(angle,R, Nhat, theta, delta)
    
    F1_star = getForce(R1_star)
    F2_star = getForce(R2_star)
    F_star = F1_star - F2_star / 2

    F_perp_star, theta_star = perpForce(F1_star, F2_star, Nhat_star)

    F = scalarRotationalForce(F_perp, theta, delta)
    dF = dScalarRotationalForce(F_star, theta_star,F0, theta, angle)
    angle_est = rotationEstimate(F0, theta, F_star, theta_star, dF)

    return angle_est




In [10]:
#Climb towards saddlepoint

In [11]:
def getEffectiveForce(angle_est, R, Nhat, theta, delta):
    R1, R2 , Nhat = rotateDimer(angle_est,R, Nhat, theta, delta)
    F1 = getForce(R1)
    F2 = getForce(R2)
    F0 = F1 - F2 / 2
    Nhat = Nhat / np.linalg.norm(Nhat)
    F_eff = F0 - 2* np.dot(F0, Nhat)* Nhat
    return F_eff, Nhat

In [12]:
view = Viewer(mep.getRodList(), width=1024, height=800)
mep.setViewer(view)
view.show()

Renderer(camera=PerspectiveCamera(aspect=1.28, children=(PointLight(color='#999999', position=(0.0, 0.0, 5.0),…

In [13]:
R = cp.getDoFs() #midpoint of dimer
N = np.random.rand(len(R)) 
Nhat = N / np.linalg.norm(N) # random unit vector
delta = 0.1 #distance of R1 and R2
for i in range(100001):
    
    
    R1 = R + delta * Nhat
    R2 = R - delta * Nhat
    
    
    F1 = getForce(R1)
    F2 = getForce(R2)
    F0 = (F1 + F2) /2 #mean force
    
    F_perp, theta = perpForce(F1, F2, Nhat)
    F_par = np.dot(F0, Nhat)* Nhat
    
    angle = estimateAngle(R, Nhat,theta, delta)
    F_eff, Nhat = getEffectiveForce(angle, R, Nhat, theta, delta)
    
    #step = min(1e-2,(np.linalg.norm(F_eff) + 1e-8))
    step = 0.01
    R = R + step * F_eff
    print(f"Contact Energy {cp.contactEnergy()}")
    cp.setDoFs(R)
    if(i % 10 == 0):
        view.update()
        print(f"it {i}, with step: {step}, F_eff: {np.linalg.norm(F_eff)} and Knot energy: {cp.energy()}")

Contact Energy 10.366298797935293
it 0, with step: 0.01, F_eff: 203.19351310563445 and Knot energy: 12.005540702475395
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 10, with step: 0.01, F_eff: 2.4347604812132735 and Knot energy: 2.105446569341031
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 20, with step: 0.01, F_eff: 1.3171481252534525 and Knot energy: 1.5135370428614057
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 30, with step: 0.01, F_eff: 0.9060332098528439 and Knot energy: 1.2853597630348892
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0

Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 350, with step: 0.01, F_eff: 0.06952457378445655 and Knot energy: 0.8613068865000202
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 360, with step: 0.01, F_eff: 0.06789055643577668 and Knot energy: 0.8605349392730829
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 370, with step: 0.01, F_eff: 0.06637265565086473 and Knot energy: 0.8597982534230636
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 380, with step: 0.01, F_eff: 0.06495776437257929 

Contact Energy 0.0
it 680, with step: 0.01, F_eff: 0.042056987196751 and Knot energy: 0.8458323706925229
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 690, with step: 0.01, F_eff: 0.04157353616288263 and Knot energy: 0.8455488463910679
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 700, with step: 0.01, F_eff: 0.041099612453956484 and Knot energy: 0.8452720725218127
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 710, with step: 0.01, F_eff: 0.04063493446888653 and Knot energy: 0.8450018463498558
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Con

Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 1030, with step: 0.01, F_eff: 0.029498430118141235 and Knot energy: 0.8388908308351523
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 1040, with step: 0.01, F_eff: 0.029240369181611183 and Knot energy: 0.8387573236123723
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 1050, with step: 0.01, F_eff: 0.028986491219750984 and Knot energy: 0.8386263077530948
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
Contact Energy 0.0
it 1060, with step: 0.01, F_eff: 0.028736706815435564 and Knot energy: 0.83849771848

Contact Energy 6.249922744765949e-06
Contact Energy 6.23788711658147e-06
Contact Energy 6.225866641536389e-06
Contact Energy 6.213861505891997e-06
Contact Energy 6.201871889359078e-06
Contact Energy 6.1898979651039715e-06
Contact Energy 6.177939900210246e-06
it 1280, with step: 0.01, F_eff: 0.02192638726730159 and Knot energy: 0.8363588645284594
Contact Energy 6.165997855826112e-06
Contact Energy 6.154071987257003e-06
Contact Energy 6.142162444285083e-06
Contact Energy 6.1302693711771175e-06
Contact Energy 6.1183929073256735e-06
Contact Energy 6.106533187027455e-06
Contact Energy 6.094690339777539e-06
Contact Energy 6.082864490444124e-06
Contact Energy 6.071055759269566e-06
Contact Energy 6.0592642624098775e-06
it 1290, with step: 0.01, F_eff: 0.0217814013490427 and Knot energy: 0.8362851600593227
Contact Energy 6.047490111788227e-06
Contact Energy 6.035733415156398e-06
Contact Energy 6.023994276574018e-06
Contact Energy 6.0122727961087785e-06
Contact Energy 6.000569070328154e-06
Conta

...

Contact Energy 3.796137243127096e-09
Contact Energy 3.796129149620578e-09
Contact Energy 3.7961210496514876e-09
Contact Energy 3.796112943228645e-09
Contact Energy 3.796104829980218e-09
Contact Energy 3.796096710198747e-09
Contact Energy 3.796088583503611e-09
Contact Energy 3.796080450404159e-09
Contact Energy 3.7960723105356394e-09
it 98880, with step: 0.01, F_eff: 0.0015697288954507676 and Knot energy: 0.8343806298596492
Contact Energy 3.796064163804581e-09
Contact Energy 3.796056010545982e-09
Contact Energy 3.796047850833857e-09
Contact Energy 3.79603968443384e-09
Contact Energy 3.7960315113882064e-09
Contact Energy 3.796023331291679e-09
Contact Energy 3.796015144791062e-09
Contact Energy 3.7960069515462705e-09
Contact Energy 3.795998751768775e-09
Contact Energy 3.795990545335302e-09
it 98890, with step: 0.01, F_eff: 0.0015693871729662784 and Knot energy: 0.8343802523021879
Contact Energy 3.795982332110132e-09
Contact Energy 3.795974112632627e-09
Contact Energy 3.795965886500943e-09

it 99080, with step: 0.01, F_eff: 0.0015629414224994015 and Knot energy: 0.8343731128614907
Contact Energy 3.794303783190561e-09
Contact Energy 3.794294342385579e-09
Contact Energy 3.794284895358591e-09
Contact Energy 3.794275442092043e-09
Contact Energy 3.794265982610625e-09
Contact Energy 3.794256517421805e-09
Contact Energy 3.794247045921273e-09
Contact Energy 3.7942375682147516e-09
Contact Energy 3.79422808431642e-09
Contact Energy 3.794218594509931e-09
it 99090, with step: 0.01, F_eff: 0.0015626046252032615 and Knot energy: 0.8343727388864737
Contact Energy 3.794209098351339e-09
Contact Energy 3.794199595754278e-09
Contact Energy 3.794190087118811e-09
Contact Energy 3.794180571907523e-09
Contact Energy 3.794171050770656e-09
Contact Energy 3.794161523387529e-09
Contact Energy 3.794151989789903e-09
Contact Energy 3.794142449882626e-09
Contact Energy 3.794132903840231e-09
Contact Energy 3.7941233513737695e-09
it 99100, with step: 0.01, F_eff: 0.001562268071226626 and Knot energy: 0.8

Contact Energy 3.791940902262441e-09
Contact Energy 3.791930075509116e-09
Contact Energy 3.791919242742117e-09
Contact Energy 3.7919084039668355e-09
Contact Energy 3.791897559556602e-09
Contact Energy 3.791886709365302e-09
Contact Energy 3.791875853440543e-09
it 99320, with step: 0.01, F_eff: 0.0015549248871508557 and Knot energy: 0.8343641860388413
Contact Energy 3.7918649919672906e-09
Contact Energy 3.791854124721857e-09
Contact Energy 3.791843252304931e-09
Contact Energy 3.7918323739380275e-09
Contact Energy 3.791821489821969e-09
Contact Energy 3.7918106003037235e-09
Contact Energy 3.7917997048990284e-09
Contact Energy 3.791788804060497e-09
Contact Energy 3.791777897238726e-09
Contact Energy 3.791766984821179e-09
it 99330, with step: 0.01, F_eff: 0.001554593853925064 and Knot energy: 0.8343638162708064
Contact Energy 3.7917560672411796e-09
Contact Energy 3.7917451437361094e-09
Contact Energy 3.7917342146670775e-09
Contact Energy 3.791723279664256e-09
Contact Energy 3.791712339097537

Contact Energy 3.789147639253936e-09
Contact Energy 3.789135491669475e-09
Contact Energy 3.789123338921205e-09
Contact Energy 3.789111181114753e-09
it 99560, with step: 0.01, F_eff: 0.0015470449090764075 and Knot energy: 0.8343553590584681
Contact Energy 3.789099017871682e-09
Contact Energy 3.7890868494824674e-09
Contact Energy 3.789074676124915e-09
Contact Energy 3.7890624972252525e-09
Contact Energy 3.789050313116147e-09
Contact Energy 3.789038123876879e-09
Contact Energy 3.789025929827903e-09
Contact Energy 3.78901373108191e-09
Contact Energy 3.789001526925913e-09
Contact Energy 3.78898931788641e-09
it 99570, with step: 0.01, F_eff: 0.0015467194861147307 and Knot energy: 0.8343549934001856
Contact Energy 3.788977103382355e-09
Contact Energy 3.788964883825869e-09
Contact Energy 3.788952658956328e-09
Contact Energy 3.788940428907627e-09
Contact Energy 3.78892819359884e-09
Contact Energy 3.788915953346776e-09
Contact Energy 3.788903707868102e-09
Contact Energy 3.788891457203337e-09
Con

it 99800, with step: 0.01, F_eff: 0.0015392978627030926 and Knot energy: 0.8343466296248178
Contact Energy 3.786035033429052e-09
Contact Energy 3.78602168264802e-09
Contact Energy 3.786008326857442e-09
Contact Energy 3.785994965951821e-09
Contact Energy 3.785981600999181e-09
Contact Energy 3.785968231214778e-09
Contact Energy 3.785954856885494e-09
Contact Energy 3.7859414782611835e-09
Contact Energy 3.785928094810558e-09
Contact Energy 3.785914706816863e-09
it 99810, with step: 0.01, F_eff: 0.0015389779018716288 and Knot energy: 0.834346267982265
Contact Energy 3.7859013142396735e-09
Contact Energy 3.785887917124831e-09
Contact Energy 3.785874515145062e-09
Contact Energy 3.785861108397159e-09
Contact Energy 3.785847697153874e-09
Contact Energy 3.7858342813413854e-09
Contact Energy 3.785820861065262e-09
Contact Energy 3.785807435908539e-09
Contact Energy 3.785794005943391e-09
Contact Energy 3.785780571539321e-09
it 99820, with step: 0.01, F_eff: 0.001538658165492512 and Knot energy: 0.8